In [1]:
import os
import json
import pickle
import pandas as pd
import numpy as np
from sklearn.linear_model import RidgeCV, LogisticRegressionCV
from sklearn.model_selection import StratifiedKFold
from tqdm.notebook import tqdm
from rca import make_binary_scoring, make_multiclass_scoring, process_categorical, best_logistic_solver, checker, k_fold_cross_val

## Loading Data

In [2]:
# Loading dictionary of dtype to embed
with open('../../data/raw/dtype_to_embed.json', 'r') as f:
    dtype_to_embed = json.load(f)
    
brain_behav_names = dtype_to_embed['brain'] + dtype_to_embed['behavior']

# Iterating through pulled_embeds and finding union of all brain and behavior vocabs
embeds_path = '../../data/raw/embeds/'
brain_behav_union = set()
for name in tqdm(brain_behav_names):
    vocab = set(pd.read_csv(embeds_path + name + '.csv', index_col=0).index)
    brain_behav_union = brain_behav_union.union(vocab)

len(brain_behav_union)  

  0%|          | 0/16 [00:00<?, ?it/s]

46238

In [3]:
# Pulling and standardising embeddings
embeds = {}
embeds_path = '../../data/raw/embeds/'
for f_name in tqdm(os.listdir(embeds_path)):
    if f_name != 'feature_overlap.csv':  # dropping since contains many NaNs
        
        embed = pd.read_csv(embeds_path + f_name, index_col=0)
        embed_name = f_name.split('.')[0]
        
        # Subsetting to brain and behavior vocab
        embed = embed.loc[embed.index.intersection(brain_behav_union)]
        
        # Standardising
        embeds[embed_name] = (embed - embed.mean()) / embed.std()

{name: embed.shape for name, embed in embeds.items()}

  0%|          | 0/26 [00:00<?, ?it/s]

{'CBOW_GoogleNews': (42830, 300),
 'PPMI_SVD_SouthFlorida': (4959, 300),
 'SVD_sim_rel': (6002, 300),
 'spherical_text_Wikipedia': (35533, 300),
 'norms_sensorimotor': (36854, 11),
 'fastText_Wiki_News': (43143, 300),
 'PPMI_SVD_EAT': (7775, 300),
 'GloVe_Twitter': (32947, 200),
 'LexVec_CommonCrawl': (44082, 300),
 'fastTextSub_OpenSub': (40607, 300),
 'eye_tracking': (7486, 6),
 'SGSoftMaxOutput_SWOW': (25442, 300),
 'morphoNLM': (32769, 50),
 'SGSoftMaxInput_SWOW': (11783, 300),
 'fMRI_text_hyper_align': (1205, 1000),
 'GloVe_Wikipedia': (39421, 300),
 'EEG_text': (3355, 104),
 'fastText_CommonCrawl': (44443, 300),
 'fMRI_speech_hyper_align': (579, 6),
 'compo_attribs': (534, 62),
 'PPMI_SVD_SWOW': (11783, 300),
 'microarray': (626, 15),
 'EEG_speech': (1591, 130),
 'GloVe_CommonCrawl': (44278, 300),
 'THINGS': (1562, 49)}

In [4]:
norms = pd.read_csv('../../data/raw/psychNorms.zip', index_col=0, compression='zip', low_memory=False)
norm_metadata = pd.read_csv('../../data/raw/psychNorms_metadata.csv', index_col='norm')
norm_metadata['associated_embed'] = norm_metadata['associated_embed'].astype(str)
norms

Freq_HAL  Freq_KF  Freq_SUBTLEXUS  Freq_SUBTLEXUK  Freq_Blog  \
'em               0.0      NaN             NaN             NaN        NaN   
'neath            0.0      NaN             NaN             NaN        NaN   
're               0.0      NaN             NaN             NaN        NaN   
'shun             0.0      NaN             NaN             NaN        NaN   
'tis              0.0      NaN             NaN             NaN        NaN   
...               ...      ...             ...             ...        ...   
shrick            NaN      NaN             NaN             NaN        NaN   
post office       NaN      NaN             NaN             NaN        NaN   
fishing rod       NaN      NaN             NaN             NaN        NaN   
March             NaN      NaN             NaN             NaN        NaN   
May               NaN      NaN             NaN             NaN        NaN   

             Freq_Twitter  Freq_News  Freq_CobW  Freq_CobS  CD_SUBTLEXUS  ...  \
'em                   NaN        NaN     1.3617     1.9138           NaN  ...   
'neath                NaN        NaN     0.0000     0.0000           NaN  ...   
're                   NaN        NaN     0.9031     1.6335           NaN  ...   
'shun                 NaN        NaN     0.0000     0.0000           NaN  ...   
'tis                  NaN        NaN     0.4771     0.6021           NaN  ...   
...                   ...        ...        ...        ...           ...  ...   
shrick                NaN        NaN        NaN        NaN           NaN  ...   
post office           NaN        NaN        NaN        NaN           NaN  ...   
fishing rod           NaN        NaN        NaN        NaN           NaN  ...   
March                 NaN        NaN        NaN        NaN           NaN  ...   
May                   NaN        NaN        NaN        NaN           NaN  ...   

             reproduction_vanarsdall  person_vanarsdall  goals_vanarsdall  \
'em                              NaN                NaN               NaN   
'neath                           NaN                NaN               NaN   
're                              NaN                NaN               NaN   
'shun                            NaN                NaN               NaN   
'tis                             NaN                NaN               NaN   
...                              ...                ...               ...   
shrick                           NaN                NaN               NaN   
post office                      NaN                NaN               NaN   
fishing rod                      NaN                NaN               NaN   
March                            NaN                NaN               NaN   
May                              NaN                NaN               NaN   

             movement_vanarsdall  concreteness_vanarsdall  \
'em                          NaN                      NaN   
'neath                       NaN                      NaN   
're                          NaN                      NaN   
'shun                        NaN                      NaN   
'tis                         NaN                      NaN   
...                          ...                      ...   
shrick                       NaN                      NaN   
post office                  NaN                      NaN   
fishing rod                  NaN                      NaN   
March                        NaN                      NaN   
May                          NaN                      NaN   

             familiarity_vanarsdall  imageability_vanarsdall  \
'em                             NaN                      NaN   
'neath                          NaN                      NaN   
're                             NaN                      NaN   
'shun                           NaN                      NaN   
'tis                            NaN                      NaN   
...                             ...                      ...   
shrick   

In [5]:
# Log transforming selected norms
with open('../../data/processed/norms_to_log.pkl', 'rb') as f:
    norms_to_log = pickle.load(f)
    norms[norms_to_log] = norms[norms_to_log].apply(np.log1p)

norms_to_log

['Nsenses_WordNet',
 'Nsenses_Wordsmyth',
 'Nmeanings_Wordsmyth',
 'Nmeanings_Websters',
 'NFeatures',
 'Sem_N',
 'Assoc_Freq_Token123',
 'Cue_SetSize',
 'LexicalD_RT_V_ELP',
 'LexicalD_RT_V_ECP',
 'LexicalD_RT_V_BLP',
 'LexicalD_RT_A_MALD',
 'LexicalD_RT_A_AELP',
 'Naming_RT_ELP',
 'SemanticD_RT_Calgary',
 'rt_khanna',
 'rt_ley',
 'rt_chiarello',
 'rt_chen',
 'aoa_rt_cortese',
 'imageability_rt_cortese',
 'rt_schock']

In [6]:
with open('../../data/raw/embed_to_dtype.json', 'r') as f:
    embed_to_type = json.load(f)
embed_to_type

{'CBOW_GoogleNews': 'text',
 'fastText_CommonCrawl': 'text',
 'fastText_Wiki_News': 'text',
 'fastTextSub_OpenSub': 'text',
 'GloVe_CommonCrawl': 'text',
 'GloVe_Twitter': 'text',
 'GloVe_Wikipedia': 'text',
 'LexVec_CommonCrawl': 'text',
 'morphoNLM': 'text',
 'spherical_text_Wikipedia': 'text',
 'eye_tracking': 'brain',
 'EEG_speech': 'brain',
 'EEG_text': 'brain',
 'fMRI_speech_hyper_align': 'brain',
 'fMRI_text_hyper_align': 'brain',
 'microarray': 'brain',
 'PPMI_SVD_SWOW': 'behavior',
 'SGSoftMaxInput_SWOW': 'behavior',
 'SGSoftMaxOutput_SWOW': 'behavior',
 'PPMI_SVD_SouthFlorida': 'behavior',
 'PPMI_SVD_EAT': 'behavior',
 'THINGS': 'behavior',
 'feature_overlap': 'behavior',
 'norms_sensorimotor': 'behavior',
 'compo_attribs': 'behavior',
 'SVD_sim_rel': 'behavior'}

## Cross Validation

In [7]:
# Ridge
min_ord, max_ord = -5, 5
alphas = np.logspace(
    min_ord, max_ord, max_ord - min_ord + 1
)
ridge = RidgeCV(alphas=alphas)

# Logistic hyperparameters
Cs = 1 / alphas
inner_cv = 5
penalty = 'l2'

# Scorers
binary_scoring = make_binary_scoring()
multiclass_scoring = make_multiclass_scoring()
continuous_scoring = {'r2': 'r2', 'neg_mse': 'neg_mean_squared_error'}

# outer_cv setting 
outer_cv, n_jobs = 5, 10

In [8]:
# RCA
rca = []
for embed_name in tqdm(embeds.keys()):
    embed = embeds[embed_name]
    
    to_print = []
    for norm_name in tqdm(norms.columns, desc=embed_name):
        
        # Aligning data
        y = norms[norm_name].dropna()
        X, y = embed.align(y, axis=0, join='inner', copy=True)
        
        # Checking norm dtype 
        norm_dtype = norm_metadata.loc[norm_name, 'type']
        
        # Solvers, scoring, estimators
        if norm_dtype in ['binary', 'multiclass']:
            X, y = process_categorical(outer_cv, inner_cv, X, y)
            
            # may have switched form multi to bin after processing
            norm_dtype = 'binary' if len(y.unique()) == 2 else 'multiclass'
            
            # Cross validation settings for logistic regression
            solver = best_logistic_solver(X, norm_dtype)
            
            # Defining logistic regression 
            estimator = LogisticRegressionCV(
                Cs=Cs, penalty=penalty, cv=StratifiedKFold(inner_cv),
                solver=solver, n_jobs=8
            )
            scoring = binary_scoring if norm_dtype == 'binary' else multiclass_scoring
        else: # continuous
            estimator, scoring = ridge, continuous_scoring
  
        # Cross validation
        associated_embed = norm_metadata.loc[norm_name, 'associated_embed']
        check = checker(embed_name, y, norm_dtype, associated_embed, outer_cv)
        if check == 'pass':
            scores = k_fold_cross_val(estimator, X, y, outer_cv, scoring, n_jobs) # stratification is automatically used for classification
            r2s, mses = scores['test_r2'], - scores['test_neg_mse']
            r2_mean, r2_sd = r2s.mean(), r2s.std()
            mse_mean, mse_sd = mses.mean(), mses.std()
        else:
            r2_mean, r2_sd = np.nan, np.nan
            mse_mean, mse_sd = np.nan, np.nan
            
        # Saving
        train_n = int(((outer_cv - 1) / outer_cv) * len(X))
        test_n = len(X) - train_n
        p = X.shape[1]
        embed_type = embed_to_type[embed_name]
        rca.append([
            embed_name, embed_type, norm_name, train_n, test_n, p, 
            r2_mean, r2_sd, mse_mean, mse_sd, check
        ])
        
        to_print.append([norm_name, train_n, r2_mean, r2_sd, check])

    to_print = pd.DataFrame(to_print, columns=['norm' , 'train_n', 'r2_mean', 'r2_sd', 'check'])
    print(to_print.sort_values('r2_mean', ascending=False).head(10))

rca = pd.DataFrame(
    rca, columns=[
        'embed', 'embed_type', 'norm', 'train_n', 'test_n', 'p', 
        'r2_mean', 'r2_sd', 'mse_mean', 'mse_sd', 'check'
    ]
)

rca.to_csv('../../data/final/rca.csv', index=False)
rca

  0%|          | 0/25 [00:00<?, ?it/s]

CBOW_GoogleNews:   0%|          | 0/292 [00:00<?, ?it/s]

/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not conver

                        norm  train_n   r2_mean     r2_sd check
283        person_vanarsdall      960  0.817393  0.019020  pass
281       thought_vanarsdall      960  0.815265  0.013993  pass
218            valence_britz      375  0.809409  0.024288  pass
219         social_des_britz      375  0.805828  0.022057  pass
284         goals_vanarsdall      960  0.796573  0.020816  pass
162          goals_wilkowski      837  0.785734  0.012998  pass
177      concreteness_hollis      828  0.784008  0.018515  pass
24              Conc_Glasgow     3672  0.781250  0.009689  pass
269     likableness_anderson      386  0.780283  0.036849  pass
282  reproduction_vanarsdall      960  0.776169  0.009854  pass


PPMI_SVD_SouthFlorida:   0%|          | 0/292 [00:00<?, ?it/s]

...

                      norm  train_n   r2_mean     r2_sd check
218          valence_britz      384  0.832397  0.096434  pass
219       social_des_britz      384  0.827537  0.084828  pass
283      person_vanarsdall      960  0.818899  0.027482  pass
281     thought_vanarsdall      960  0.813102  0.019946  pass
284       goals_vanarsdall      960  0.806998  0.021245  pass
213  tabooness_janschewitz      359  0.793416  0.050916  pass
269   likableness_anderson      405  0.773479  0.090871  pass
162        goals_wilkowski      842  0.762251  0.087604  pass
255   likableness_chandler      644  0.755676  0.083720  pass
175         valence_hollis      829  0.755092  0.072602  pass


THINGS:   0%|          | 0/292 [00:00<?, ?it/s]

/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
/datapool-1/homepoint/zhussain/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_sag.py:352: ConvergenceWarning: The max_iter was reached which means the coef_ did not conver

                        norm  train_n   r2_mean     r2_sd check
105         Biomotion_Binder      128  0.872332  0.042505  pass
280        living_vanarsdall      376  0.841733  0.019199  pass
111              Body_Binder      128  0.834058  0.052231  pass
282  reproduction_vanarsdall      376  0.827012  0.027135  pass
35            Gustatory_Lanc     1235  0.813969  0.040591  pass
124             Taste_Binder      128  0.809113  0.100118  pass
122             Music_Binder      128  0.760995  0.067979  pass
285      movement_vanarsdall      376  0.723601  0.033689  pass
281       thought_vanarsdall      376  0.721569  0.080251  pass
131              Path_Binder      128  0.715336  0.068376  pass


embed embed_type                     norm  train_n  test_n  \
0     CBOW_GoogleNews       text                 Freq_HAL    28012    7003   
1     CBOW_GoogleNews       text                  Freq_KF    19285    4822   
2     CBOW_GoogleNews       text           Freq_SUBTLEXUS    28636    7159   
3     CBOW_GoogleNews       text           Freq_SUBTLEXUK    29316    7330   
4     CBOW_GoogleNews       text                Freq_Blog    31876    7969   
...               ...        ...                      ...      ...     ...   
7295           THINGS   behavior   familiarity_vanarsdall      376      95   
7296           THINGS   behavior  imageability_vanarsdall      376      95   
7297           THINGS   behavior         familiarity_fear      173      44   
7298           THINGS   behavior                 aoa_fear      173      44   
7299           THINGS   behavior        imageability_fear      173      44   

        p   r2_mean     r2_sd     mse_mean      mse_sd check  
0     300  0.522118  0.008398     2.715453    0.072527  pass  
1     300  0.500425  0.009710     0.156666    0.004775  pass  
2     300  0.537265  0.009814     0.361345    0.007803  pass  
3     300  0.545643  0.008416     0.446042    0.009075  pass  
4     300  0.523700  0.008448     0.400166    0.009345  pass  
...   ...       ...       ...          ...         ...   ...  
7295   49  0.091050  0.077868  3216.050320  580.598768  pass  
7296   49  0.074112  0.090266  1317.411401  292.505564  pass  
7297   49  0.151637  0.158767     0.782185    0.220500  pass  
7298   49  0.015012  0.129597     0.514519    0.043528  pass  
7299   49 -0.023230  0.101781     0.262705    0.049417  pass  

[7300 rows x 11 columns]